In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pickle
import os
import decoupler as dc
from scipy.stats import mannwhitneyu
import re
%load_ext rpy2.ipython

In [53]:
%%R
suppressMessages({
    library(tidyverse)
    library(ggfortify)
    library(limma)
    library(cowplot)
    library(vsn)
    library(ggrepel)
    library(ggforce)
    library(patchwork)
})

In [54]:
translator_df = pd.read_csv('data/processed_data/translator_df.csv')
uniprot_to_symbol = translator_df.set_index('uniprot')['symbol'].to_dict()
symbol_to_uniprot = translator_df.set_index('symbol')['uniprot'].to_dict()

In [55]:
de_df = pd.read_csv('data/processed_data/egf_data.csv.gz')
de_df['residue'] = de_df['site_id'].str.extract(r'_([STY])\d+')
de_df['protein'] = de_df['site_id'].str.extract(r'(.+)_')
de_df['symbol'] = de_df['protein'].map(uniprot_to_symbol)
de_df['residue_site'] = de_df['site_id'].str.extract(r'_(.+)')
de_df['symbol_site'] = de_df['symbol'] + '_' + de_df['residue_site']
de_df['treatment_time'] = de_df['comparison'].str.extract(r'(\d+)min')
de_df['study_comparison'] = de_df['study'] + ' ' + de_df['treatment_time'] + 'min'

In [56]:
kinlib_cutoff = 95
phosformer_cutoff = 0.65
cache_file = '/tmp/kinsubs_{}_{}.pkn'.format(kinlib_cutoff, phosformer_cutoff)
if os.path.exists(cache_file):
    pkn = pickle.load(open(cache_file, 'rb'))
else:
    literature = pd.read_csv('data/processed_data/omnipath_enzsub.csv.gz')
    kinlibrary = pd.read_csv('data/processed_data/kinase_library.csv.gz')
    phosformer = pd.read_csv('data/processed_data/phosformer_preds.csv.gz')
    kinlib_nints = kinlibrary.shape[0]
    phosformer_nints = phosformer.shape[0]
    literature = literature.groupby(['source', 'target']).agg({'n_references': 'max'}).reset_index()
    literature['resource'] = 'literature'
    literature['score'] = 1
    literature = literature[['source', 'target', 'score', 'resource', 'n_references']].drop_duplicates()
    kinlibrary = kinlibrary[kinlibrary['score'] >= kinlib_cutoff].copy()
    kinlib_filtins = kinlibrary.shape[0]
    print('Kinase library: {}% of interactions kept'.format(kinlib_filtins / kinlib_nints * 100))
    kinlibrary = kinlibrary.groupby(['source', 'target']).agg({'score': 'max'}).reset_index()
    kinlibrary['score'] = kinlibrary['score'] / kinlibrary['score'].max()
    kinlibrary['resource'] = 'kinlibrary'
    phosformer = phosformer[phosformer['score'] >= phosformer_cutoff].copy()
    phosformer_filtins = phosformer.shape[0]
    print('Phosformer: {}% of interactions kept'.format(phosformer_filtins / phosformer_nints * 100))
    phosformer = phosformer.groupby(['source', 'target']).agg({'score': 'max'}).reset_index()
    phosformer['resource'] = 'phosformer'
    phosformer['score'] = phosformer['score'] / phosformer['score'].max()
    pkn = pd.concat([literature, kinlibrary, phosformer])
    coral_kins = pd.read_csv('data/processed_data/coral_df.csv')
    human_kins = coral_kins['id.uniprot'].unique()
    pkn = pkn[pkn['source'].isin(human_kins)].copy()
    pickle.dump(pkn, open(cache_file, 'wb'))
pkn = pkn.rename(columns = {'score': 'weight'})
pkn_all = pkn.groupby(['source', 'target']).agg({'weight': 'max'}).reset_index()
pkn_all['resource'] = 'combined'
pkn = pd.concat([pkn, pkn_all])

In [57]:
coverage_df = []
for resource in ['literature', 'kinlibrary', 'phosformer', 'combined']:
    if resource == 'all':
        pkn_filtered = pkn.copy()
    else:
        pkn_filtered = pkn[pkn['resource'] == resource].copy()
    
    pkn_sites = pkn_filtered['target'].unique()
    for study in de_df['study'].unique():
        all_sites = de_df[de_df['study'] == study]['site_id'].unique()
        proportion_covered = len(set(pkn_sites).intersection(all_sites)) / len(all_sites)
        coverage_df.append({'resource': resource, 'study': study, 'proportion_covered': proportion_covered})
coverage_df = pd.DataFrame(coverage_df)

In [ ]:
coverage_df.groupby('resource').agg({'proportion_covered': 'mean'}).reset_index()

In [59]:
color_map = {
    'no resource': 'gray',
    'literature': '#fde725',
    'kinlibrary': '#35b779',
    'phosformer': '#31688e',
    'combined': '#440154'
}
coverage_df = coverage_df.sort_values('proportion_covered', ascending=False)
coverage_df.to_csv('/tmp/coverage_df.csv', index=False)

In [ ]:
%%R
toplot <- read_csv('/tmp/coverage_df.csv')
int_cols <- c('no resource' = 'gray', 'literature'= '#fde725','kinlibrary'='#31688e', 'phosformer' = '#35b779', 'combined'='#440154')

p <- toplot %>%
  mutate(resource = fct_reorder(resource, proportion_covered)) %>%
  ggplot(aes(y = resource, x = proportion_covered, fill = resource)) +
  scale_fill_manual(values = int_cols) +
  geom_boxplot(color = 'black', size = .5) +
  geom_sina() +
  xlab('Proportion of sites covered') +
  ylab('Resource') +
  ggtitle('Coverage') +
  theme_cowplot()+
  theme(plot.title = element_text(hjust = 0.5)) 
ggsave('figures/main/egf_coverage.pdf', p, width = 5, height = 3.5, dpi = 300, bg = 'transparent')
p

In [ ]:
to_dc_data = de_df.copy()
to_dc_data = to_dc_data.pivot_table(index='site_id', columns='study_comparison', values='logFC').fillna(0).T
kin_estimates = []
for resource in ['literature', 'kinlibrary', 'phosformer', 'combined']:
    if resource == 'all':
        pkn_dc = pkn.copy()
    else:
        pkn_dc = pkn[pkn['resource'] == resource].copy()
    dc_result = dc.dense_run(dc.run_ulm, net = pkn_dc, mat = to_dc_data, verbose = True)
    dc_df = pd.DataFrame(dc_result[0].T).reset_index().melt(id_vars='index', var_name='study_comparison', value_name='activity').rename(columns={'index': 'kinase'})
    dc_df['resource'] = resource
    kin_estimates.append(dc_df)
kin_estimates = pd.concat(kin_estimates)

In [62]:
kin_norm = kin_estimates.copy()
kin_norm['norm_activity'] = kin_norm.groupby(['study_comparison', 'resource'])['activity'].transform(lambda x: x / x.abs().max())
kin_norm['study'] = kin_norm['study_comparison'].apply(lambda x: re.match(r'(.+?\))', x).group(1))
egf_proteins = pd.read_csv('data/processed_data/signor_egf.tsv', sep='\t')
egf_proteins = list(set(egf_proteins['IDA_expl']).union(set(egf_proteins['IDB_expl'])))
kin_norm['is_egf'] = kin_norm['kinase'].isin(egf_proteins)
kin_norm['symbol'] = kin_norm['kinase'].map(uniprot_to_symbol)
kin_norm.to_csv('/tmp/kin_annot.csv', index=False)

In [63]:
toplot = []
for i, int_resource in enumerate(['site level','literature',  'phosformer', 'kinlibrary', 'combined']):
    if int_resource == 'site level':
        de_tocor = de_df[['site_id', 'study', 'logFC']].copy()
        de_tocor = de_tocor.groupby(['site_id', 'study']).agg({'logFC': 'mean'}).reset_index()
        de_tocor = de_tocor.pivot_table(index='site_id', columns='study', values='logFC')
        de_tocor = de_tocor.dropna()
        corr_result = de_tocor.corr( method='pearson')
        n_features = de_tocor.shape[0]
    else:
        kin_data = kin_norm[kin_norm['resource'] == int_resource].copy()
        kin_data = kin_data.groupby(['study', 'kinase']).agg({'activity': 'mean'}).reset_index()
        kin_wide = kin_data.pivot_table(index='study', columns='kinase', values='activity').T
        kin_wide = kin_wide.dropna()
        corr_result = kin_wide.corr( method='pearson')
        n_features = kin_wide.shape[0]
    cor_df = corr_result.copy()
    mask = np.triu(np.ones_like(cor_df, dtype=bool))
    cor_df = cor_df.mask(mask)
    cor_df = cor_df.reset_index().melt(id_vars='study', var_name='study_2', value_name='correlation').rename(columns={'index': 'study_1'}).dropna()
    cor_df['resource'] = int_resource 
    cor_df['n_feats'] = n_features
    toplot.append(cor_df)
toplot = pd.concat(toplot)
toplot.to_csv('/tmp/toplot_cor.csv')

In [ ]:
toplot.groupby('resource').agg({'correlation': 'mean'}).reset_index()

In [ ]:
%%R -w 800 -h 800
cordf <- read_csv('/tmp/toplot_cor.csv') %>%
  arrange(study, study_2) %>%
  mutate(study = fct_rev(fct_inorder(study)),
         study_2 = fct_rev(fct_inorder(study_2)))

p <- cordf %>%
  ggplot(aes(x = study, y = study_2, fill = correlation)) +
  geom_tile() +
  facet_wrap(vars(resource)) +
  geom_tile() +
  scale_fill_viridis_c(option = 'viridis', name = 'Pearson') +
  geom_label(aes(label = round(correlation, 2)), fill = 'white') +
  theme_cowplot() +
  theme(axis.text.x = element_text(angle = 90, hjust = 1)) 

ggsave('figures/supp/detailed_kinase_correlation.png', p, width = 12, height = 8, dpi = 300, bg = 'transparent')
p

In [ ]:
toplot.groupby('resource').agg({'correlation': 'mean'}).reset_index()

In [ ]:
%%R
toplot <- read_csv('/tmp/toplot_cor.csv') %>%
  mutate(int_labels = paste0(resource, '\n(N=', n_feats, ')')) 

int_cols <- c('gray', '#fde725', '#35b779','#31688e',  '#440154')
names(int_cols) <- c('site level', 'literature', 'kinlibrary', 'phosformer', 'combined')

p <- toplot %>%
  mutate(resource = factor(resource, levels = c(
    'site level','literature', 'phosformer', 'kinlibrary', 'combined'
  ))) %>%
  arrange(resource) %>%
  ggplot(aes(x = correlation, y = resource, fill = resource)) +
  geom_violin(alpha = 0.5) +
  scale_y_discrete(labels = unique(toplot$int_labels)) +
  geom_boxplot(alpha = 0.5) +
  geom_sina() +
  scale_fill_manual(values = int_cols) +
  theme_cowplot() +
  ggtitle('Correlation') + ylab('Resource') +
  xlab('Pearson R') +
  theme(plot.title = element_text(hjust = 0.5))

ggsave('figures/main/kinase_level_correlations.pdf', p, width = 5, height = 3.5, dpi = 300, bg = 'transparent')
p

In [68]:
resdf = []
for int_study in kin_norm['study_comparison'].unique():
    for int_resource in kin_norm['resource'].unique():
        study_df = kin_norm[(kin_norm['study_comparison'] == int_study) & (kin_norm['resource'] == int_resource)].dropna()
        egf_kins = study_df[study_df['is_egf']]
        non_egf_kins = study_df[~study_df['is_egf']]
        res = mannwhitneyu(egf_kins['activity'].abs(), non_egf_kins['activity'].abs())
        diff = egf_kins['activity'].abs().mean() - non_egf_kins['activity'].abs().mean()
        resdf.append([int_resource, int_study, res.pvalue, diff])
resdf = pd.DataFrame(resdf, columns=['resource', 'study_comparison', 'pvalue', 'diff'])
resdf.to_csv('/tmp/egf_kins.csv')

In [ ]:
resdf.groupby('study_comparison').agg({'diff': 'mean'}).reset_index().sort_values('diff', ascending=False)

In [ ]:
toline = resdf[resdf['study_comparison'].str.contains('This study')]
toline['mins'] = toline['study_comparison'].str.extract(r'(\d+)min')
toline['mins'] = toline['mins'].astype(int)
toline['study'] = toline['study_comparison'].str.extract(r'(.+?)\d+min')
toline.to_csv('/tmp/toline.csv')

In [ ]:
%%R -w 600 -h 250
toline <- read_csv('/tmp/toline.csv')
int_cols <- c('no resource' = 'gray', 'literature'= '#fde725','kinlibrary'='#31688e', 'phosformer' = '#35b779', 'combined'='#440154')  

p<-ggplot(toline, aes(x = mins, y = diff, color = resource, fill = resource)) +
  geom_line() +
  facet_grid(cols = vars(study), scales = 'free') +
  geom_point(pch = 21, color ='black') +
  scale_color_manual(values = int_cols) +
  scale_fill_manual(values = int_cols) +
  theme_cowplot() +
  xlab('Time (minutes)') +
  ylab('Absolute kinase\nactivity difference')

ggsave('figures/supp/kinase_over_time.png', p, width = 9, height = 4, dpi = 300, bg = 'transparent')
p

In [ ]:
%%R -w 700 -h 400
toplot <- read_csv('/tmp/egf_kins.csv') %>%
  mutate(padj = p.adjust(pvalue, method = 'BH')) %>%
  mutate(is_sig = ifelse(padj <= 0.05, '*', '')) %>%
  mutate(study_comparison = fct_reorder(study_comparison, diff, .fun=mean, .desc = TRUE)) %>%
  mutate(resource = fct_reorder(resource, diff,.fun=mean,  .desc = TRUE)) 

mean_per_study <- toplot %>%
  group_by(study_comparison) %>%
  summarise(mean = mean(diff, na.rm = TRUE)) %>%
  mutate(study_comparison = fct_reorder(study_comparison, mean, .desc = TRUE))

mean_per_resource <- toplot %>%
  group_by(resource) %>%
  summarise(mean = mean(diff, na.rm = TRUE)) %>%
  mutate(resource = fct_reorder(resource, mean, .desc = TRUE))

dp <- toplot %>%
  ggplot(aes(x = study_comparison, y = resource, fill = diff)) +
  geom_point(pch = 21, size = 5) +
  geom_text(aes(label= is_sig)) +
  scale_fill_viridis_c(name = 'Absolute\nactivity\ndifference') +
  theme_cowplot() +
  theme(axis.text.x = element_text(angle = 45, hjust = 1)) +
  xlab('Contrast') + ylab('Resource') +
  theme(legend.position = 'left')

right_bp <- mean_per_resource %>%
  ggplot(aes(y = resource, x = mean)) +
  geom_bar(stat = 'identity', fill = 'lightgray', color = 'black') +
  theme_cowplot() +
  theme(axis.title.y = element_blank(),
        axis.text.y = element_blank(),
        axis.ticks.y = element_blank(),
        axis.title.x = element_blank(),
        axis.text.x = element_text(size = 7))

top_bp <- mean_per_study %>%
  ggplot(aes(x = study_comparison, y = mean)) +
  geom_bar(stat = 'identity', fill = 'lightgray', color = 'black') +
  theme_cowplot() +
  theme(axis.title.x = element_blank(),
        axis.text.x = element_blank(),
        axis.ticks.x = element_blank(),
        axis.title.y = element_blank(),
        axis.text.y = element_text(size = 7))
        
p <-(top_bp + plot_spacer() + plot_layout(widths = c(1, 0.05))) /  (dp + right_bp + plot_layout(widths = c(1, 0.05))) +
  plot_layout(heights = c(0.4, 1))
ggsave('figures/main/egf_kinase_diff.pdf', p, width = 10, height = 4.5, dpi = 300, bg = 'transparent')
p

In [46]:
kin_norm.to_csv('/tmp/kin_norm.csv')

In [51]:
kin_norm.dropna().to_csv('supp_tables/3_kinase_activities.csv.gz', index=False, compression='gzip')

In [ ]:
%%R -w 500 -h 250
kinnorm <- read_csv('/tmp/kin_norm.csv') %>%
  group_by(symbol, resource) %>%
  mutate(mean_act = mean(norm_activity, na.rm = TRUE)) %>%
  ungroup()

toplot <- kinnorm %>%
  dplyr::select(symbol, resource, mean_act, is_egf) %>%
  dplyr::distinct() %>%
  arrange(desc(abs(mean_act))) %>%
  group_by(resource, is_egf) %>%
  slice_head(n = 5) %>%
  ungroup() %>%
  mutate(yvalue = paste0(resource, '_', symbol)) %>%
  mutate(yvalue = fct_reorder(yvalue, abs(mean_act))) %>%
  mutate(resource = factor(resource, levels = c('literature', 'phosformer', 'kinlibrary','combined')))

 p <- toplot %>%
   ggplot(aes(y = yvalue, x = mean_act, fill = is_egf)) +
   geom_bar(stat = 'identity') +
   scale_fill_manual(values = c('grey', 'red'), name = 'In\nEGF pathway') +
   facet_wrap(vars(resource), nrow = 1, scales = 'free') +
   scale_y_discrete(labels = function(x) gsub('.*_', '', x)) +
   theme_cowplot() +
   xlab('Mean activity') + ylab('Kinase') +
theme(axis.text.x = element_text(angle = 45, hjust = 1)) 

ggsave('figures/main/top_kinases.pdf', p, width = 10, height = 3, dpi = 300, bg = 'transparent')
p

In [ ]:
%%R -w 1000 -h 800
toplot <- read_csv('/tmp/kin_norm.csv') %>%
   dplyr::filter(is_egf) %>%
   drop_na() %>%
  mutate(study = str_extract(study_comparison, '.*\\)')) %>%
  mutate(comparison = str_extract(study_comparison, '\\((.*)', group = 1)) %>%
  mutate(time =str_extract(comparison,  '([0-9]+)min', 1) %>% as.numeric()) %>%
  arrange(study,time) %>%
  mutate(study_comparison = fct_rev(fct_inorder(study_comparison))) %>%
  mutate(resource = factor(resource, levels = c('literature', 'phosformer', 'kinlibrary','combined'))) %>%
  mutate(symbol = fct_reorder(symbol, activity))

p <- toplot %>%
  ggplot(aes(x = symbol, y = study_comparison, fill = norm_activity)) +
  facet_wrap(vars(resource)) +
  geom_tile(color = 'black') +
  scale_fill_gradient2( low = "blue", mid = "white", high = "red", midpoint = 0, limits = c(-1, 1),
                       oob = scales::squish) +
  guides(x = guide_axis(angle = 60)) + 
  xlab('Kinase') + ylab('Contrast') +
  theme_cowplot()
             
ggsave('figures/supp/egf_kinase_activity.png', p, width = 11, height = 8.5)
p